In [131]:
import pandas as pd
from collections import Counter, namedtuple
import urllib.request
from razdel import tokenize, sentenize
from string import punctuation
from tqdm import tqdm
import csv
import fasttext
import numpy as np
import itertools
from transformers import AutoTokenizer
from sklearn.linear_model import LogisticRegression

# Домашнее задание
## Yes/No Questions

В этом домашнем задании вы будете работать с корпусом BoolQ. Корпус состоит из вопросов, предполагающих бинарный ответ (да / нет), абзацев из Википедии,  содержащих ответ на вопрос, заголовка статьи, из которой извлечен абзац и непосредственно ответа (true / false).

Корпус описан в статье:

Christopher Clark, Kenton Lee, Ming-Wei Chang, Tom Kwiatkowski, Michael Collins, Kristina Toutanova
BoolQ: Exploring the Surprising Difficulty of Natural Yes/No Questions

https://arxiv.org/abs/1905.10044


Корпус (train-dev split) доступен в репозитории проекта:  https://github.com/google-research-datasets/boolean-questions

Используйте для обучения train часть корпуса, для валидации и тестирования – dev часть. 

Каждый бонус пункт оцениватся в 1 балл. 

### Пример вопроса: 
question: is batman and robin a sequel to batman forever

title: Batman & Robin (film)

answer: true

passage: With the box office success of Batman Forever in June 1995, Warner Bros. immediately commissioned a sequel. They hired director Joel Schumacher and writer Akiva Goldsman to reprise their duties the following August, and decided it was best to fast track production for a June 1997 target release date, which is a break from the usual 3-year gap between films. Schumacher wanted to homage both the broad camp style of the 1960s television series and the work of Dick Sprang. The storyline of Batman & Robin was conceived by Schumacher and Goldsman during pre-production on A Time to Kill. Portions of Mr. Freeze's back-story were based on the Batman: The Animated Series episode ''Heart of Ice'', written by Paul Dini.

## ПРАВИЛА
1. Домашнее задание выполняется в группе до 2-х человек.
2. Домашнее задание оформляется в виде отчета в ipython-тетрадке. 
3. Отчет должен содержать: нумерацию заданий и пунктов, которые вы выполнили, код решения, и понятное пошаговое описание того, что вы сделали. Отчет должен быть написан в академическом стиле, без излишнего использования сленга и с соблюдением норм русского языка.
4. Не стоит копировать фрагменты лекций, статей и Википедии в ваш отчет.

## Часть 1. [1 балл] Эксплоративный анализ
1. Посчитайте долю yes и no классов в корпусе
2. Оцените среднюю длину вопроса
3. Оцените среднюю длину параграфа
4. Предположите, по каким эвристикам были собраны вопросы (или найдите ответ в статье). Продемонстриуйте, как эти эвристики повлияли на структуру корпуса. 

In [2]:
train_data_df = pd.read_json('train.jsonl', lines=True, orient='records')
dev_data_df = pd.read_json('dev.jsonl', lines=True, orient='records')
train_data_df.head(3)

question                title  \
0    do iran and afghanistan speak the same language     Persian language   
1  do good samaritan laws protect those who help ...   Good Samaritan law   
2  is windows movie maker part of windows essentials  Windows Movie Maker   

   answer                                            passage  
0    True  Persian (/ˈpɜːrʒən, -ʃən/), also known by its ...  
1    True  Good Samaritan laws offer legal protection to ...  
2    True  Windows Movie Maker (formerly known as Windows...

##### 1)

In [15]:
a_1 = train_data_df.answer.value_counts()\
                   .reset_index()\
                   .rename(columns={'index':'answer', 'answer':'cnt'})
a_1['rt'] = a_1['cnt']/a_1['cnt'].sum()
a_1['rt'] = a_1['rt'].round(2)
a_1

answer   cnt    rt
0    True  5874  0.62
1   False  3553  0.38

##### 2)

In [21]:
train_data_df.question.apply(len).mean().round(0)

44.0

##### 3)

In [22]:
train_data_df.passage.apply(len).mean().round(0)

566.0

##### 4) <br>
вопросы начинаются со слов-индикаторов

In [41]:
a_4 = train_data_df.question.apply(lambda x: x.split()[0])\
                            .value_counts()\
                            .reset_index()\
                            .rename(columns={'index':'1st_qst_word','question':'cnt'})
a_4 = a_4[a_4.cnt>5]
a_4['rt'] = (a_4.cnt / len(train_data_df)).round(2)
a_4

1st_qst_word   cnt    rt
0            is  4190  0.44
1           can  1136  0.12
2          does   952  0.10
3           are   693  0.07
4            do   664  0.07
5           did   461  0.05
6           was   335  0.04
7           has   302  0.03
8          will   181  0.02
9           the    91  0.01
10         have    70  0.01
11           in    35  0.00
12         were    25  0.00
13           if    17  0.00
14            a    16  0.00
15         what    11  0.00
16         when    10  0.00
17        could     9  0.00

## Часть 2. [1 балл] Baseline
1. Оцените accuracy точность совсем простого базового решения: присвоить каждой паре вопрос-ответ в dev части самый частый класс из train части
2. Оцените accuracy чуть более сложного базового решения: fasttext на текстах, состоящих из склееных вопросов и абзацев (' '.join([question, passage]))

Почему fasttext плохо справляется с этой задачей?

##### 1)

In [69]:
most_frq_ans = Counter(train_data_df.answer).most_common(1)[0][0]
(dev_data_df.answer == most_frq_ans).sum() / len(dev_data_df)

0.6217125382262997

##### 2)

https://towardsdatascience.com/fasttext-for-text-classification-a4b38cbff27c

preprocessing

In [8]:
# train
train_text = [  ' '.join([question, passage])
                for question, passage 
                in zip(train_data_df.question.tolist(), train_data_df.passage.tolist())]

for i in tqdm(range(len(train_text))):
    text_i = []
    for sent in sentenize(train_text[i]):
        sent_i = [ j.text.lower() for j in tokenize(sent.text) if j.text not in list(punctuation)]
        text_i.extend(sent_i)
    train_text[i] = text_i
    
# dev
dev_text = [  ' '.join([question, passage])
                for question, passage 
                in zip(dev_data_df.question.tolist(), dev_data_df.passage.tolist())]

for i in tqdm(range(len(dev_text))):
    text_i = []
    for sent in sentenize(dev_text[i]):
        sent_i = [ j.text.lower() for j in tokenize(sent.text) if j.text not in list(punctuation)]
        text_i.extend(sent_i)
    dev_text[i] = text_i

100%|█████████████████████████████████████| 3270/3270 [00:02<00:00, 1111.13it/s]


saving txt-files

In [46]:
# train
train_dataset = pd.DataFrame({'text': train_text, 'target': train_data_df.answer.tolist()})
train_dataset['text'] = train_dataset['text'].apply(lambda x: ' '.join(x))
train_dataset['target'] = train_dataset['target'].apply(lambda x: '__label__' + str(x))
train_dataset[['target', 'text']].to_csv('train.txt', 
                                         index = False, 
                                         sep = ' ',
                                         header = None, 
                                         quoting = csv.QUOTE_NONE, 
                                         quotechar = "", 
                                         escapechar = " ")
# dev
dev_dataset = pd.DataFrame({'text': dev_text, 'target': dev_data_df.answer.tolist()})
dev_dataset['text'] = dev_dataset['text'].apply(lambda x: ' '.join(x))
dev_dataset['target'] = dev_dataset['target'].apply(lambda x: '__label__' + str(x))
dev_dataset[['target', 'text']].to_csv('dev.txt', 
                                         index = False, 
                                         sep = ' ',
                                         header = None, 
                                         quoting = csv.QUOTE_NONE, 
                                         quotechar = "", 
                                         escapechar = " ")

training

In [47]:
model = fasttext.train_supervised('train.txt', wordNgrams = 2)

Read 0M words
Number of words:  47170
Number of labels: 2
Progress: 100.0% words/sec/thread:  995967 lr:  0.000000 avg.loss:  0.654642 ETA:   0h 0m 0s


test

In [49]:
model.test('dev.txt')   

(3270, 0.6290519877675841, 0.6290519877675841)

In [54]:
predict = model.predict(dev_dataset['text'].iloc[0])[0]
predict

('__label__True',)

## Часть 3. [1 балл] Используем эмбеддинги предложений
1. Постройте BERT эмбеддинги вопроса и абзаца. Обучите логистическую регрессию на конкатенированных эмбеддингах вопроса и абзаца и оцените accuracy этого решения. 

[bonus] Используйте другие модели эмбеддингов, доступные, например, в библиотеке 🤗 Transformers. Какая модель эмбеддингов даст лучшие результаты?

[bonus] Предложите метод аугментации данных и продемонстрируйте его эффективность. 

##### 1) BERT embedding

In [93]:
tokenizer = AutoTokenizer.from_pretrained('nlptown/bert-base-multilingual-uncased-sentiment')

# train
train_dataset = train_data_df[['question', 'passage', 'answer']].copy()
train_dataset['question'] = train_dataset.question.apply(lambda x: tokenizer(x)['input_ids']) #tokenizer.tokenize(x))
train_dataset['question'] = train_dataset.question.apply(lambda x: x[:30] + [0]*(30-len(x[:30]))) 
train_dataset['passage'] = train_dataset.passage.apply(lambda x: tokenizer(x)['input_ids'])
train_dataset['passage'] = train_dataset.passage.apply(lambda x: x[:1000] + [0]*(1000-len(x[:1000])))
train_dataset['q&p'] = train_dataset[['question', 'passage']].apply(lambda x: x[0]+x[1], axis=1)

# dev
dev_dataset = dev_data_df[['question', 'passage', 'answer']].copy()
dev_dataset['question'] = dev_dataset.question.apply(lambda x: tokenizer(x)['input_ids'])
dev_dataset['question'] = dev_dataset.question.apply(lambda x: x[:30] + [0]*(30-len(x[:30]))) 
dev_dataset['passage'] = dev_dataset.passage.apply(lambda x: tokenizer(x)['input_ids'])
dev_dataset['passage'] = dev_dataset.passage.apply(lambda x: x[:1000] + [0]*(1000-len(x[:1000])))
dev_dataset['q&p'] = dev_dataset[['question', 'passage']].apply(lambda x: x[0]+x[1], axis=1)

Token indices sequence length is longer than the specified maximum sequence length for this model (928 > 512). Running this sequence through the model will result in indexing errors


model

In [126]:
X_train, y_train = np.array(train_dataset['q&p'].tolist()), train_dataset['answer'].astype(int)
clf = LogisticRegression(random_state=0).fit(X_train, y_train)
predict = clf.predict(X_train)
print('train accuracy:', (predict == y_train).sum() / len(y_train))

train accuracy: 0.6375304975071603


/Users/16971921/.conda/envs/py38_venv/lib/python3.8/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


test

In [128]:
X_test, y_test = np.array(dev_dataset['q&p'].tolist()), dev_dataset['answer'].astype(int)
predict = clf.predict(X_test)
print('test accuracy:', (predict == y_test).sum() / len(y_test))

test accuracy: 0.6067278287461774


## Часть 3. [3 балла] DrQA-подобная архитектура

Основана на статье: Reading Wikipedia to Answer Open-Domain Questions

Danqi Chen, Adam Fisch, Jason Weston, Antoine Bordes

https://arxiv.org/abs/1704.00051

Архитектура DrQA предложена для задачи SQuAD, но легко может быть адаптирована к текущему заданию. Модель состоит из следующих блоков:
1. Кодировщик абзаца [paragraph encoding] – LSTM, получаящая на вход вектора слов, состоящие из: 
* эмбеддинга слова (w2v или fasttext)
* дополнительных признаков-индикаторов, кодирующих в виде one-hot векторов часть речи слова, является ли оно именованной сущностью или нет, встречается ли слово в вопросе или нет 
* выровненного эмбеддинга вопроса, получаемого с использованием soft attention между эмбеддингами слов из абзаца и эмбеддингом вопроса.

$f_{align}(p_i) = \sum_j􏰂 a_{i,j} E(q_j)$, где $E(q_j)$ – эмбеддинг слова из вопроса. Формула для $a_{i,j}$ приведена в статье. 

2. Кодировщик вопроса [question encoding] – LSTM, получаящая на вход эмбеддинги слов из вопроса. Выход кодировщика: $q = 􏰂\sum_j􏰂  b_j q_j$. Формула для $b_{j}$ приведена в статье. 

3. Слой предсказания. 

Предложите, как можно было модифицировать последний слой предсказания в архитектуре DrQA, с учетом того, что итоговое предсказание – это метка yes / no, предсказание которой проще, чем предсказание спана ответа для SQuAD.

Оцените качество этой модели для решения задачи. 

[bonus] Замените входные эмбеддинги и все дополнительные признаки, используемые кодировщиками, на BERT эмбеддинги. Улучшит ли это качество результатов?

##### 1)

In [ ]:
pd.read_json('train.jsonl', lines=True, orient='records')

In [137]:
Sample = namedtuple("Sample", "question, passage, labels")

def get_dataset(path_file: list):
    samples = []
    file = pd.read_json(path_file, lines=True, orient='records')
    question = file.question.tolist()
    passage = file.passage.tolist()
    
    for i in tqdm(range(len(file))):
        #question
        text_i = []
        for sent in sentenize(question[i]):
            sent_i = [ j.text.lower() for j in tokenize(sent.text) if j.text not in list(punctuation)]
            text_i.extend(sent_i)
        question[i] = text_i
        
        #question
        text_i = []
        for sent in sentenize(passage[i]):
            sent_i = [ j.text.lower() for j in tokenize(sent.text) if j.text not in list(punctuation)]
            text_i.extend(sent_i)
        passage[i] = text_i
    
        labels = file.answer.astype(int)
    
        sample = Sample(question, passage, labels)
        samples.append(sample)

    return samples

In [142]:
# a = get_dataset('train.jsonl')
a[0]

Sample(question=[['do', 'iran', 'and', 'afghanistan', 'speak', 'the', 'same', 'language'], ['do', 'good', 'samaritan', 'laws', 'protect', 'those', 'who', 'help', 'at', 'an', 'accident'], ['is', 'windows', 'movie', 'maker', 'part', 'of', 'windows', 'essentials'], ['is', 'confectionary', 'sugar', 'the', 'same', 'as', 'powdered', 'sugar'], ['is', 'elder', 'scrolls', 'online', 'the', 'same', 'as', 'skyrim'], ['can', 'you', 'use', 'oyster', 'card', 'at', 'epsom', 'station'], ['will', 'there', 'be', 'a', 'season', '4', 'of', 'da', 'vinci', 's', 'demons'], ['is', 'the', 'federal', 'court', 'the', 'same', 'as', 'the', 'supreme', 'court'], ['did', 'abraham', 'lincoln', 'write', 'the', 'letter', 'in', 'saving', 'private', 'ryan'], ['is', 'batman', 'and', 'robin', 'a', 'sequel', 'to', 'batman', 'forever'], ['is', 'a', 'wolverine', 'the', 'same', 'as', 'a', 'badger'], ['will', 'there', 'be', 'a', 'green', 'lantern', '2', 'movie'], ['does', 'the', 'icc', 'has', 'jurisdiction', 'in', 'the', 'united'

In [ ]:
# max_seq_len=500
# max_char_seq_len=40
# batch_size=32
def get_next_gen_batch(samples, max_seq_len=512, max_char_seq_len=40, batch_size=2):
    indices = np.arange(len(train))
    np.random.shuffle(indices)
    batch_begin = 0
    with tqdm(total=len(train)) as pbar:
      while batch_begin < len(train):
          batch_indices = indices[batch_begin: batch_begin + batch_size]
          batch_words = []
          batch_chars = []
          batch_labels = []
          batch_max_len = 0
          batch_masks = [] #for CRF
          for data_ind in batch_indices:
              sample = train[data_ind] #беру одно предложение
              words = torch.zeros(max_seq_len, dtype=torch.long).cuda()
              inputs = torch.zeros((max_seq_len, max_char_seq_len), dtype=torch.long).cuda()
              for token_num, token in enumerate(sample.tokens[:max_seq_len]): #цикл по токенам предложения, обрезанного до max_seq_len
                  #слова
                  words[token_num] = word_set.index(token) if token in word_set else word_set.index('<unk>')
                  #символы
                  for char_num, char in enumerate(token[:max_char_seq_len]):
                      inputs[token_num][char_num] = char_set.index(char) if char in char_set else char_set.index('<unk>')
              labels = sample.labels[:max_seq_len]         #аналогично с labels
              masks = [1]*len(labels) + [0]*(max_seq_len - len(labels)) 
              labels += [0] * (max_seq_len - len(labels))  #аналогично с labels
              
              batch_words.append(words)
              batch_chars.append(inputs)
              batch_labels.append(labels)
              batch_masks.append(masks)
              
          batch_begin += batch_size
          pbar.update(batch_size)
          
          batch_words = torch.stack(batch_words)
          batch_chars = torch.stack(batch_chars)
          labels = torch.cuda.LongTensor(batch_labels)
          batch_masks = torch.tensor(batch_masks).cuda()>0
          yield batch_indices, batch_words, batch_chars, labels, batch_masks

## Часть 4. [3 балла] BiDAF-подобная архитектура

Основана на статье: Bidirectional Attention Flow for Machine Comprehension

Minjoon Seo, Aniruddha Kembhavi, Ali Farhadi, Hannaneh Hajishirzi

https://arxiv.org/abs/1611.01603

Архитектура BiDAF предложена для задачи SQuAD, но легко может быть адаптирована к текущему заданию. Модель состоит из следующих блоков:
1. Кодировщик  получает на вход два представления слова: эмбеддинг слова и полученное из CNN посимвольное представление слова. Кодировщики для вопроса и для параграфа одинаковы. 
2. Слой внимания (детальное описание приведено в статье, см. пункт Attention Flow Layer)
3. Промежуточный слой, который получает на вход контекстуализированные эмбеддинги слов из параграфа, состоящие из трех частей (выход кодировщика параграфа,   Query2Context (один вектор) и Context2Query (матрица) выравнивания

4. Слой предсказания. 

Предложите, как можно было модифицировать последний слой предсказания в архитектуре BiDAF, с учетом того, что итоговое предсказание – это метка yes / no, предсказание которой проще, чем предсказание спана ответа для SQuAD.

Оцените качество этой модели для решения задачи. 

[bonus] Замените входные эмбеддинги и все дополнительные признаки, используемые кодировщиками, на BERT эмбеддинги. Улучшит ли это качество результатов?

Сравнение DrQA и BiDAF:
    
![](https://www.researchgate.net/profile/Felix_Wu6/publication/321069852/figure/fig1/AS:560800147881984@1510716582560/Schematic-layouts-of-the-BiDAF-left-and-DrQA-right-architectures-We-propose-to.png)

## Часть 5. [1 балл] Итоги
Напишите краткое резюме проделанной работы. Сравните результаты всех разработанных моделей. Что помогло вам в выполнении работы, чего не хватало?

# draft

In [ ]:
# urllib.request.urlretrieve('https://dl.fbaipublicfiles.com/fasttext/vectors-english/wiki-news-300d-1M.vec.zip', 
#                            'pre-trained-fasttext.zip')

# from zipfile import ZipFile
# with ZipFile('pre-trained-fasttext.zip', 'r') as f:
#     f.extractall('pre-trained-fasttext')